<center><img src="https://github.com/pandas-dev/pandas/raw/main/web/pandas/static/img/pandas.svg" alt="pandas Logo" style="width: 800px;"/></center>

# Pandas 2: NYS Mesonet Map
---

## Overview
In this notebook, we'll use Cartopy, Matplotlib, and Pandas (with a little help from [MetPy](https://unidata.github.io/MetPy)) to read in, manipulate, and visualize data from the [New York State Mesonet](https://www2.nysmesonet.org).

We'll focus on a particular time on the evening of 1 September 2021, when the remnants of Hurricane Ida were impacting the greater New York City region.

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Matplotlib | Necessary | |
| Cartopy | Necessary | |
| Pandas  | Necessary | Intro |
| MetPy | Helpful | |

* **Time to learn**: 30 minutes

___
## Imports

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from cartopy import crs as ccrs
from cartopy import feature as cfeature
from metpy.calc import wind_components
from metpy.units import units
from metpy.plots import StationPlot

Create Pandas `DataFrame` objects based on two csv files; one contains the site locations, while the other contains the hourly data.

In [ ]:
nysm_sites = pd.read_csv('/spare11/atm533/data/nysm_sites.csv')
nysm_data = pd.read_csv('/spare11/atm533/data/nysm_data_2021090202.csv')

Create `Series` objects for several columns from the two `DataFrames`.

First, remind ourselves of the column names for these two `DataFrames`.

In [ ]:
nysm_sites.columns

In [ ]:
nysm_data.columns

Create several `Series` objects for particular columns of interest. Pay attention to which `DataFrame` provides the particular `Series`!

In [ ]:
stid = nysm_sites['stid']
lats = nysm_sites['lat']
lons = nysm_sites['lon']

time = nysm_data['time']
tmpc = nysm_data['temp_2m [degC]']
rh   = nysm_data['relative_humidity [percent]']
pres = nysm_data['station_pressure [mbar]']
wspd = nysm_data['max_wind_speed_prop [m/s]']
drct = nysm_data['wind_direction_prop [degrees]']
pinc = nysm_data['precip_incremental [mm]']
ptot = nysm_data['precip_local [mm]']
pint = nysm_data['precip_max_intensity [mm/min]']

Examine one or more of these `Series`.

In [ ]:
tmpc

<div class="alert alert-warning">
    <b>Exercise:</b> Read in at least one additional <code>Series</code> object.</div>

In [ ]:
# Write your code below


<div class="alert alert-info">
    <b>Tip:</b> Each of these <code>Series</code> objects contain data stored as <b>NumPy</b> arrays. As a result, we can take advantage of <i>broadcasting</i> to perform operations on all array elements without needing to construct a Python <code>for</code> loop. </div>

Convert the temperature and wind speed arrays to Fahrenheit and knots, respectively.

In [ ]:
tmpf = tmpc * 1.8 + 32
wspk = wspd * 1.94384

Examine the new `Series`. Note that every element of the array has been calculated using the arithemtic above ... in just one line of code per `Series`!

In [ ]:
tmpf

<div class="alert alert-warning">
    <b>Note:</b>Notice that the <i>metadata</i> did not change to reflect the change in units! That is something we'd have to change manually, via the <code>Series</code>' <i>name</i> attribute:</div>

In [ ]:
tmpf.name = 'temp_2m [degF]'

In [ ]:
tmpf

Next, use another statistical *method* available to `Series`: in this case, the maximum value among all elements of the array.

In [ ]:
wspk.max()

Our goal is to make a map of NYSM observations, which includes the wind velocity. The convention is to plot wind velocity using wind barbs. The **MetPy** library allows us to not only make such a map, but perform a variety of meteorologically-relevant calculations and diagnostics. Here, we will use such a calculation, which will determine the two scalar components of wind velocity (*u* and *v*), from wind speed and direction. We will use MetPy's `wind_components` method. 

This method requires us to do the following:
1. Extract the Numpy arrays from the windspeed and direction `Series` objects via the `values` attribute
2. Attach units to these arrays using MetPy's `units` class

We can accomplish everything in this single line of code:

In [ ]:
u, v = wind_components(wspk.values * units.knots, drct.values * units.degree)

Take a look at one of the output components:

In [ ]:
u

<div class="alert alert-info">
    <b>Tip:</b> This is a unique type of object: not only does it have values, aka <i>magnitude</i>, but it also has <i>Units</i> attached. This is a very nice property, since it will make calculations that require awareness of units much easier!</div>

Now, let's plot several of the meteorological values on a map. We will use **Matplotlib** and **Cartopy**, as well as **MetPy**'s `StationPlot` method.

### Plot the map, centered over NYS, with add some geographic features, and the mesonet data.
***
### In the 2nd Cartopy notebook from last week, we used the `ax.scatter` and `ax.text` methods to plot markers for the stations and their site id's. The latter method does not provide many options for text justification relative to a point. For a meteorological surface station plot, let's take advantage of the `Metpy` package, and its StationPlot method.

#### <b>Be patient: this may take a minute or so to plot, if you chose the highest resolution for the shapefiles!</b>

In [ ]:
# Set the domain for defining the plot region.
latN = 45.2
latS = 40.2
lonW = -80.0
lonE = -72.0
cLat = (latN + latS)/2
cLon = (lonW + lonE )/2

res = '50m'
proj = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)

fig = plt.figure(figsize=(18,12),dpi=150) # Increase the dots per inch from default 100 to make plot easier to read
ax = fig.add_subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.add_feature (cfeature.LAND.with_scale(res))
ax.add_feature (cfeature.OCEAN.with_scale(res))
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.LAKES.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res));

# Create a station plot pointing to an Axes to draw on as well as the location of points
stationplot = StationPlot(ax, lons, lats, transform=ccrs.PlateCarree(),
                          fontsize=8)

stationplot.plot_parameter('NW', tmpf, color='red')
stationplot.plot_parameter('SW', rh, color='green')
stationplot.plot_parameter('NE', pres, color='purple')
stationplot.plot_barb(u, v,zorder=2) # zorder value set so wind barbs will display over lake features
ax.set_title ('Temperature ($^\circ$F), RH (%), Station Pressure (hPa), Peak 5-min Wind (kts) 0200 UTC 02 September 2021');

What if we wanted to plot sea-level pressure (SLP) instead of station pressure? In this case, we can apply what's called a **reduction to sea-level pressure** formula. This formula requires station elevation (accounting for sensor height) in meters, temperature in Kelvin, and station pressure in hectopascals. We assume each NYSM station has its sensor height .5 meters above ground level.

<div class="alert alert-info">
    <b>Tip:</b> At present, <b>MetPy</b> does not yet have a function that reduces station pressure to SLP, so we will do a <i>units-unaware</i> calculation.</div>

In [ ]:
elev = nysm_sites['elevation']
sensorHeight = .5
# Reduce station pressure to SLP. Source: https://www.sandhurstweather.org.uk/barometric.pdf 
slp = pres/np.exp(-1*(elev+sensorHeight)/((tmpc+273.15) * 29.263))

In [ ]:
slp

Make a new map, substituting SLP for station pressure. We will also use the convention of the three least-significant digits to represent SLP in hectopascals.

<div class="alert alert-info">
    <b>Examples: 1018.4</b> hPa would be plotted as <b>184</b>, while <b>977.2</b> hPa would be plotted as <b>772.</b></div>

In [ ]:
fig = plt.figure(figsize=(18,12),dpi=150)
ax = fig.add_subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.add_feature (cfeature.LAND.with_scale(res))
ax.add_feature (cfeature.OCEAN.with_scale(res))
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.LAKES.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res));

# Create a station plot pointing to an Axes to draw on as well as the location of points
stationplot = StationPlot(ax, lons, lats, transform=ccrs.PlateCarree(),
                          fontsize=8)

stationplot.plot_parameter('NW', tmpf, color='red')
stationplot.plot_parameter('SW', rh, color='green')
# A more complex example uses a custom formatter to control how the sea-level pressure
# values are plotted. This uses the standard trailing 3-digits of the pressure value
# in tenths of millibars.
stationplot.plot_parameter('NE', slp, color='purple', formatter=lambda v: format(10 * v, '.0f')[-3:])
stationplot.plot_barb(u, v,zorder=10)
ax.set_title ('Temperature ($^\circ$F), RH (%), SLP (hPa), Peak 5-min Wind (kts) 0200 UTC 02 September 2021');

<div class="alert alert-warning">
    <b>For further thought:</b> Think about how you might calculate and then display dewpoint instead of relative humidity.

---
## Summary
* Multiple `Series` can be constructed from multiple `DataFrames`
* A single mathematical function can be applied (*broadcasted*) to all array elements in a `Series`
* The **MetPy** library provides methods to assign physical units to numerical arrays and perform units-aware calculations
* **MetPy**'s `StationPlot` method offers a customized use of **Matplotlib**'s **Pyplot** library to plot several meteorologically-relevant parameters centered about several geo-referenced points.
### What's Next?
In the next notebook, we will explore several ways in Pandas to reference particular rows, columns, and/or row-column pairs in a Pandas `DataFrame`.
## Resources and References
1. [Hurricane Ida](https://en.wikipedia.org/wiki/Hurricane_Ida)
1. [MetPy's *calc* library](https://unidata.github.io/MetPy/latest/api/generated/metpy.calc.html)
1. [MetPy's *units* library](https://unidata.github.io/MetPy/latest/api/generated/metpy.units.html)
1. [Sea-level pressure reduction formula (source: Sandhurst Weather site)](https://www.sandhurstweather.org.uk/barometric.pdf)
1. [MetPy's *StationPlot* class](https://unidata.github.io/MetPy/latest/api/generated/metpy.plots.StationPlot.html#metpy.plots.StationPlot)